In [1]:
from ortools.constraint_solver import pywrapcp, routing_enums_pb2
from vehi_rout.utils.helper_utils import get_penalty_list, get_values_not_in_second_list
from vehi_rout.utils.visualization import visualize_routes_per_vehicle
from vehi_rout.utils.data_utils import get_demand_df, update_demand_dic, load_matrix_df, get_demand_matrix_df, load_df
from vehi_rout.utils.route_utils import sort_nodes_by_distance
from vehi_rout.constant import *
from vehi_rout.utils.visualization import visualize_routes_per_vehicle, save_route_details_to_csv, print_route_summary

load c:\Users\HP\Desktop\E-Vision-Projects\Vehicle_Routing\venv\Lib\site-packages\ortools\.libs\zlib1.dll...
load c:\Users\HP\Desktop\E-Vision-Projects\Vehicle_Routing\venv\Lib\site-packages\ortools\.libs\abseil_dll.dll...
load c:\Users\HP\Desktop\E-Vision-Projects\Vehicle_Routing\venv\Lib\site-packages\ortools\.libs\utf8_validity.dll...
load c:\Users\HP\Desktop\E-Vision-Projects\Vehicle_Routing\venv\Lib\site-packages\ortools\.libs\re2.dll...
load c:\Users\HP\Desktop\E-Vision-Projects\Vehicle_Routing\venv\Lib\site-packages\ortools\.libs\libprotobuf.dll...
load c:\Users\HP\Desktop\E-Vision-Projects\Vehicle_Routing\venv\Lib\site-packages\ortools\.libs\highs.dll...
load c:\Users\HP\Desktop\E-Vision-Projects\Vehicle_Routing\venv\Lib\site-packages\ortools\.libs\ortools.dll...
Loaded 465 cached routes from ../data/csv/route_cache.csv


In [123]:
TOTAL_DAYS = 6
MAX_VISITS_PER_VEHICLE = [15]*2 + [15]*2 + [15]*2 + [15]*2

DISTANCE_BASE_PENALTY = 1000
MAX_DISTANCE_PER_VEHICLE = [600]*2 + [600]*2 + [600]*2 + [1200]*2

DEPOT = 0

In [124]:
def print_solution(manager, routing, solution, data, day):
    total_distance = 0  # Changed from total_time to total_distance
    visited_nodes = set()
    route_dict = {}  # Dictionary to store route details for each vehicle
    
    print(f"\nDay {day + 1} Routes (Penalty per unvisited demand unit: {data['penalties'][1]} units):")
    for vehicle_id in range(data["num_vehicles"]):
        index = routing.Start(vehicle_id)
        plan_output = f"Route for vehicle {vehicle_id}:\n"
        route_distance = 0  # Changed from route_time to route_distance
        num_visits = 0
        route_nodes = []  # List to store the sequence of nodes for this vehicle
        previous_node = None
        
        while not routing.IsEnd(index):
            node = manager.IndexToNode(index)
            original_node = data["node_mapping"][node]
            visited_nodes.add(original_node)
            route_nodes.append(original_node)
            plan_output += f" {original_node} ->"
            if previous_node is not None:
                arc_distance = int(data["distance_matrix"][previous_node][node])  # Changed from time_matrix to distance_matrix
                route_distance += arc_distance
            previous_node = node
            index = solution.Value(routing.NextVar(index))
            if original_node != data["depot"]:
                num_visits += 1
        
        node = manager.IndexToNode(index)
        original_node = data["node_mapping"][node]
        visited_nodes.add(original_node)
        route_nodes.append(original_node)
        plan_output += f" {original_node}\n"
        if previous_node is not None:
            arc_distance = int(data["distance_matrix"][previous_node][node])  # Changed from time_matrix to distance_matrix
            route_distance += arc_distance
        
        plan_output += f"Distance of the route: {route_distance} km\n"  # Changed from Time to Distance, assumed km
        max_distance = data["max_distance_per_vehicle"][vehicle_id]  # Changed from max_time_per_vehicle to max_distance_per_vehicle
        plan_output += f"Within limit: {'Yes' if route_distance <= max_distance else 'No'} (Max: {max_distance} km)\n"  # Changed units to km
        plan_output += f"Stops visited: {num_visits-1}/{data['max_visits_per_vehicle'][vehicle_id]}\n"
        
        # Store route details in the dictionary
        route_dict[vehicle_id] = {
            "route_nodes": route_nodes,
            "route_distance": route_distance,  # Changed from route_time to route_distance
            "max_distance_limit": max_distance,  # Changed from max_time_limit to max_distance_limit
            "within_limit": route_distance <= max_distance,
            "num_visits": num_visits,
            "max_visits_limit": data["max_visits_per_vehicle"][vehicle_id]
        }
        
        print(plan_output)
        total_distance = max(total_distance, route_distance)  # Changed from total_time to total_distance
    
    print(f"Maximum route distance for Day {day + 1}: {total_distance} km")  # Changed from time to distance
    
    return visited_nodes, route_dict  # Return both visited_nodes and route_dict

In [125]:
# In data_model.vrp_data_model.py
def create_data_model(full_matrix, nodes_to_visit, demand_dict, penalty_lis, use_distance=False):
    data = {}
    node_indices = [0] + [i for i, code in enumerate(full_matrix.index) if code in demand_dict['key']]
    nodes_to_use = [node_indices[0]] + [i for i in node_indices[1:] if i in nodes_to_visit]
    data["num_vehicles"] = len(MAX_DISTANCE_PER_VEHICLE)
    data["depot"] = 0
    if use_distance:
        # Construct distance matrix from full_matrix
        data["distance_matrix"] = [[full_matrix.iloc[i][j] for j in nodes_to_use] for i in nodes_to_use]
        data["max_distance_per_vehicle"] = MAX_DISTANCE_PER_VEHICLE  
    else:
        # Original time matrix (for backward compatibility)
        data["time_matrix"] = [[full_matrix.iloc[i][j] for j in nodes_to_use] for i in nodes_to_use]
        data["max_time_per_vehicle"] = MAX_TIME_PER_VEHICLE 
        
    data["demands"] = [0] + [demand_dict.get(full_matrix.index[i], 1) for i in nodes_to_use[1:]]  # Demand at each node
    data["node_mapping"] = [full_matrix.index[i] for i in nodes_to_use] #{i: node for i, node in enumerate([0] + nodes_to_visit)}  # Mapping of indices to nodes
    data["max_visits_per_vehicle"] = MAX_VISITS_PER_VEHICLE 
    data["penalties"] = [0] + penalty_lis
    return data

In [126]:
def solve_vrp_for_day(full_matrix, nodes_to_visit, day, demand_dict, penalty_lis):
    # Assuming create_data_model now returns a distance_matrix instead of time_matrix
    data = create_data_model(full_matrix, nodes_to_visit, demand_dict,penalty_lis, use_distance=True)  # Adjust create_data_model
    manager = pywrapcp.RoutingIndexManager(len(data["distance_matrix"]), data["num_vehicles"], data["depot"])
    routing = pywrapcp.RoutingModel(manager)

    def distance_callback(from_index, to_index):
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        distance = int(data["distance_matrix"][from_node][to_node])  # Use distance instead of time
        return distance

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)

    # Distance dimension (replacing Time dimension)
    routing.AddDimension(
        transit_callback_index,
        0,
        max(data["max_distance_per_vehicle"]),  # New max distance limit per vehicle
        True,
        "Distance"
    )
    distance_dimension = routing.GetDimensionOrDie("Distance")
    for vehicle_id in range(data["num_vehicles"]):
        end_index = routing.End(vehicle_id)
        distance_dimension.CumulVar(end_index).SetMax(data["max_distance_per_vehicle"][vehicle_id])  # Set distance limit

    # Demand dimension remains unchanged
    def demand_callback(from_index):
        return data["demands"][manager.IndexToNode(from_index)]

    demand_callback_index = routing.RegisterUnaryTransitCallback(demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,
        data["max_visits_per_vehicle"],
        True,
        "Visits"
    )

    # Optional nodes with demand-based penalty (unchanged)
    for node in range(1, len(data["distance_matrix"])):
        routing.AddDisjunction([manager.NodeToIndex(node)], data["penalties"][node])

    # Search parameters (unchanged)
    search_parameters = pywrapcp.DefaultRoutingSearchParameters()
    search_parameters.first_solution_strategy = (
        routing_enums_pb2.FirstSolutionStrategy.PATH_CHEAPEST_ARC)
    search_parameters.local_search_metaheuristic = (
        routing_enums_pb2.LocalSearchMetaheuristic.GUIDED_LOCAL_SEARCH)
    search_parameters.time_limit.seconds = 30

    solution = routing.SolveWithParameters(search_parameters)
    if solution:
        return print_solution(manager, routing, solution, data, day)
    else:
        print(f"No solution found for Day {day + 1}!")
        return set()

In [127]:
demand_df = get_demand_df(
     today_path='../data/orders/03-03-2025-PO.csv',
    #  wait_path='../data/orders/next_day_demand.csv'
    # today_path='data/day-01.csv'
    )

demand_df.shape

(454, 8)

In [128]:
if demand_df['CODE'].dtype in ['float', 'int', 'int64']:
    demand_df['CODE'] = demand_df['CODE'].astype(int)
    demand_df['CODE'] = demand_df['CODE'].astype(str)
    print('Converting to Object')

In [129]:
master_mat_df = load_matrix_df(path='../data/master/osrm_distance_matrix.csv')

In [130]:
demand_mat_df = get_demand_matrix_df(master_mat_df,demand_df, 0)

In [131]:
demand_mat_df.shape

(455, 455)

In [132]:
demand_dict = update_demand_dic(demand_df)

In [133]:
len(demand_dict['key'])

454

In [134]:
len(demand_dict['po_date'])

454

In [135]:
today = '2025-03-06'
penalty_lis = get_penalty_list(demand_dict, DISTANCE_BASE_PENALTY, TOTAL_DAYS, today)

Penalty for 3: 500
Penalty for 4: 500
Penalty for 5: 500
Penalty for 10: 500
Penalty for 105: 500
Penalty for 106: 500
Penalty for 108: 500
Penalty for 109: 500
Penalty for 110: 500
Penalty for 111: 500
Penalty for 112: 500
Penalty for 113: 500
Penalty for 114: 500
Penalty for 115: 500
Penalty for 116: 500
Penalty for 117: 500
Penalty for 119: 500
Penalty for 121: 500
Penalty for 122: 500
Penalty for 123: 500
Penalty for 127: 500
Penalty for 128: 500
Penalty for 14: 500
Penalty for 150: 500
Penalty for 152: 500
Penalty for 156: 500
Penalty for 161: 500
Penalty for 163: 500
Penalty for 167: 500
Penalty for 168: 500
Penalty for 171: 500
Penalty for 172: 500
Penalty for 174: 500
Penalty for 175: 500
Penalty for 181: 500
Penalty for 188: 500
Penalty for 190: 500
Penalty for 191: 500
Penalty for 22: 500
Penalty for 23: 500
Penalty for 24: 500
Penalty for 25: 500
Penalty for 26: 500
Penalty for 27: 500
Penalty for 76: 500
Penalty for 79: 500
Penalty for 80: 500
Penalty for 14001: 500
Penalty

In [136]:
# new_lis = []
# for i in penalty_lis:
#     new_lis.append(int(i)*100)

In [137]:
# penalty_lis = new_lis

In [138]:
demand_sort_nodes = sort_nodes_by_distance(demand_mat_df.values)

In [139]:
nodes_to_visit = sorted(demand_sort_nodes[:])

In [140]:
visited_node, route_dict = solve_vrp_for_day(demand_mat_df, nodes_to_visit, 1, demand_dict, penalty_lis)


Day 2 Routes (Penalty per unvisited demand unit: 500 units):
Route for vehicle 0:
 0 -> SGEM -> 1545 -> SCSL -> 1759 -> 1746 -> 1301 -> 1776 -> 1896 -> 1614 -> SCWP -> SCGT -> 1745 -> 172 -> SCMU -> SGKY -> 0
Distance of the route: 34 km
Within limit: Yes (Max: 600 km)
Stops visited: 15/15

Route for vehicle 1:
 0 -> 171 -> 14013 -> 1137 -> SCMY -> SCKE -> 1818 -> 1672 -> 1608 -> 1105 -> 1826 -> SCCC -> 1005 -> 1108 -> SCK7 -> 1555 -> 0
Distance of the route: 46 km
Within limit: Yes (Max: 600 km)
Stops visited: 15/15

Route for vehicle 2:
 0 -> 1728 -> 1497 -> 1872 -> 1471 -> 1320 -> SCCR -> SCSJ -> SCRJ -> SCNW -> 14008 -> 1761 -> 1323 -> 1859 -> 1446 -> 1145 -> 0
Distance of the route: 36 km
Within limit: Yes (Max: 600 km)
Stops visited: 15/15

Route for vehicle 3:
 0 -> 150 -> SGRA -> SGMH -> 3 -> 117 -> 14015 -> SGWA -> SGKR -> SGTY -> 14 -> SGKB -> SGKG -> SGMQ -> SGEL -> SGK5 -> 0
Distance of the route: 33 km
Within limit: Yes (Max: 600 km)
Stops visited: 15/15

Route for vehicl

In [141]:
not_visited_codes = get_values_not_in_second_list(demand_df['CODE'], list(visited_node))

not_visited_codes_str = list(map(str, not_visited_codes))
# Filter the dataframe
sub_df = demand_df[demand_df['CODE'].isin(not_visited_codes_str)]
print(sub_df.shape)
# sub_df.to_csv('../data/orders/next_day_demand.csv', index=False)

(334, 8)


In [142]:
import folium
import pandas as pd

def visualize_all_locations(df):
    """
    Visualize all locations from a CSV file on a folium map.
    :param csv_file_path: Path to the CSV file containing location data
    :return: folium.Map object
    """
    # Load the CSV data into a DataFrame
    # try:
    #     df = df
    # except Exception as e:
    #     print(f"Error loading CSV file {csv_file_path}: {e}")
    #     return None
    try:
        # Create a map centered at the mean of all latitudes and longitudes
        map_center = [df['LATITUDE'].mean(), df['LONGITUDE'].mean()]
        m = folium.Map(location=map_center, zoom_start=10)
    except Exception as e:
        print(f"Error getting gps data: {e}")
        return None

    # Add a marker for each location
    for _, row in df.iterrows():
        folium.Marker(
            location=[row['LATITUDE'], row['LONGITUDE']],
            popup=f"CODE: {row['CODE']}<br>LOCATION: {row['LOCATION']}<br>ADDRESS: {row['ADDRESS']}<br>BRAND: {row['BRAND']}",
            icon=folium.Icon(color='blue', icon='info-sign')
        ).add_to(m)

    # Add title
    title_html = '<h3 align="center" style="font-size:16px">All Locations Map</h3>'
    m.get_root().html.add_child(folium.Element(title_html))

    return m

In [143]:
master_gps_df = load_df('../data/master/master_gps.csv')

In [144]:
total_distance = 0
for veh in route_dict.keys():
    print(f"Vehicle id: {veh}")
    path = ''
    for code in route_dict[veh]['route_nodes']:
        if code == '0':
            loc_name = "SMAK"
        else:
            loc = master_gps_df.loc[master_gps_df['CODE']==code]
            if len(loc) is None:
                loc_name = ["SMAK"]
            loc_name = loc['LOCATION'].values[0]
        
        path += f'{loc_name} ({code}) --> '
    path += f"Route Distance: {route_dict[veh]['route_distance']}km (Max: {route_dict[veh]['max_distance_limit']}km) Visits: {route_dict[veh]['num_visits']-1} (Max: {route_dict[veh]['max_visits_limit']})"
    total_distance += route_dict[veh]['route_distance']
    print(path)
    print('\n')
print(f"Total distance for all vehicles: {total_distance}km")

Vehicle id: 0
SMAK (0) --> Enderamulla (SGEM) --> FC GLORIOUS RESIDENCE (1545) --> Shangri-La Mall (SCSL) --> EX MARADANA 02 (1759) --> EX MALIGAWATTE2 (1746) --> EX MALIGAWATTE (1301) --> EX MALIGAWATTE 03 (1776) --> EX ORION CITY (1896) --> FC KOLONNAWA 02 (1614) --> Wellampitiya (SCWP) --> Gothatuwa (SCGT) --> EX RAHULA JUNCTION (1745) --> Mulleriyawa Daily (172) --> Mulleriyawa -Angoda (SCMU) --> Kelaniya (SGKY) --> SMAK (0) --> Route Distance: 34km (Max: 600km) Visits: 15 (Max: 15)


Vehicle id: 1
SMAK (0) --> Kandana Daily (171) --> KANDANA (14013) --> FC MUTUWAL (1137) --> Mattakuliya (SCMY) --> Kotahena (SCKE) --> EX PORT AUTHORITY (1818) --> FC SLAVE ISLAND (1672) --> FC KOLLUPITIYA 02 (1608) --> FC COLPETTY (1105) --> EX YMCA (1826) --> Crescat (SCCC) --> FC FORT (1005) --> FC KOTAHENA (1108) --> Kotahena 2 (SCK7) --> FC BLOEMENDHAL (1555) --> SMAK (0) --> Route Distance: 46km (Max: 600km) Visits: 15 (Max: 15)


Vehicle id: 2
SMAK (0) --> EX ASCON RESIDENCE (1728) --> FC DEMA

In [24]:
import pandas as pd

In [25]:
SMAK_KADAWATHA = (7.0038321,79.9394804)

smak_data = {
    "CODE":'0',
    "LOCATION":"SMAK",
    "ADDRESS":"Smak, Kadawatha, Western Province, Sri Lanka",
    "LATITUDE":SMAK_KADAWATHA[0],
    "LONGITUDE":SMAK_KADAWATHA[1]
}


master_df = pd.concat(
    [
        pd.DataFrame(smak_data, index=[0]),
        master_gps_df
    ],
    ignore_index=True
)

In [28]:
map_obj_2 = visualize_routes_per_vehicle(master_df, route_dict, 1)

Processing route for vehicle 0: ['0', '1880', '1783', '1616', '1434', '1891', '1448', '1429', '1288', '1584', '1684', '1688', '1687', '0']
Using cached path for 0 to 1880
Added path from 0 to 1880 with 2974 points
Using cached path for 1880 to 1783
Added path from 1880 to 1783 with 204 points
Using cached path for 1783 to 1616
Added path from 1783 to 1616 with 42 points
Using cached path for 1616 to 1434
Added path from 1616 to 1434 with 31 points
Fetching path from 1434 ((7.9353523, 81.0180545)) to 1891 ((7.9213276, 81.5246705))
Path cached for 1434 to 1891: [[7.936558, 81.018298], [7.936417, 81.019014], [7.93642, 81.019116], [7.936486, 81.019167], [7.936723, 81.019226]]... (total 793 points)
Added path from 1434 to 1891 with 793 points
Fetching path from 1891 ((7.9213276, 81.5246705)) to 1448 ((7.7768972, 81.6042028))
Path cached for 1891 to 1448: [[7.921273, 81.524807], [7.921864, 81.525051], [7.922052, 81.525109], [7.922022, 81.525257], [7.921854, 81.525731]]... (total 314 points)


#### Day 01

In [31]:
map_obj_2[0]

In [32]:
map_obj_2[1]

In [33]:
map_obj_2[2]

In [34]:
map_obj_2[3]

In [35]:
map_obj_2[4]

In [36]:
map_obj_2[5]

In [37]:
map_obj_2[6]

In [38]:
map_obj_2[7]

#### Day 02

In [64]:
map_obj_2[0]

In [65]:
map_obj_2[1]

In [71]:
map_obj_2[2]

In [66]:
map_obj_2[3]

In [67]:
map_obj_2[4]

In [68]:
map_obj_2[5]

In [69]:
map_obj_2[6]

In [70]:
map_obj_2[7]

#### Day 03

In [93]:
map_obj_2[0]

In [94]:
map_obj_2[1]

In [95]:
map_obj_2[2]

In [96]:
map_obj_2[3]

In [97]:
map_obj_2[4]

In [98]:
map_obj_2[5]

In [99]:
map_obj_2[6]

In [100]:
map_obj_2[7]

#### Day 04

In [122]:
map_obj_2[0]

In [123]:
map_obj_2[1]

In [124]:
map_obj_2[2]

In [125]:
map_obj_2[3]

In [126]:
map_obj_2[4]

In [127]:
map_obj_2[5]

In [128]:
map_obj_2[6]

In [129]:
map_obj_2[7]

#### Day 05

In [29]:
map_obj_2[0]

In [30]:
map_obj_2[1]

In [31]:
map_obj_2[3]

In [32]:
map_obj_2[4]

In [33]:
map_obj_2[5]

In [34]:
map_obj_2[7]